## Forward (filtering) algorithm and marginal likelihood computation

Remember filtering:

$$\alpha_t(x_t) = p(x_t | y_{1:t}) = \frac{p(y_t|x_t) p(x_t|y_{1:t-1})}{p(y_t | y_{1:t-1})}.$$

Set $\alpha_{t|t-1}(x_t) = p(x_t | y_{1:t-1})$ (predictive distribution).

The filtering can be expressed as,

\begin{align}
p(x_t | y_{1:t-1}) &= \sum_{x_{t-1}} p(x_t | x_{t-1}) p(x_{t-1} | y_{1:t-1}) \\
&= P_{.,x_t} \alpha_{t-1}.
\end{align}

In matrix form: $p(x_t | y_{1:t-1}) = (P^T \alpha_{t-1})(x_t)$.

The denominator is $p(y_t | y_{1:t-1}) = \sum_{x_t} p(y_t | x_t) p(x_t | y_{1:t-1})$.

The marginal is given by $p(y_{1:T}) = \prod_t p(y_t | y_{1:t-1})$.

Base case $t = 1$: compute

- $\alpha_{1|0}(j) = p(x_1 = j | \emptyset) = \mu(j)$;
- $\tilde{\alpha}_1(j) = p(y_1 | x_1) \alpha_{1|0}(j) = p(y_1 | x_1) p(x_1) = p(y_1, x_1)$;
- $m_1 = p(y_1) = \sum_j \tilde{\alpha}_1(j) = \sum_{j} p(x_1=j, y_1)$.
- $\alpha_1(j) = \tilde{\alpha}_1(j) / \sum_i \tilde{\alpha}_1(j) = p(x_1 | y_1)$.

For $t > 1$: compute

- $\alpha_{t|t-1} = p(x_t = j | y_{1:t-1}) = P^T \alpha_{t-1}$;
- $\tilde{\alpha}_t(j) = p(y_t | x_t) \alpha_{t|t-1}(j) = p(y_t | x_t) p(x_t | y_{1:t-1}) = p(y_t, x_t | y_{1:t-1})$;
- $m_t = p(y_t | y_{1:t-1}) = \sum_j \tilde{\alpha}_t(j)$.
- $\alpha_t = \tilde{\alpha}_t(j) / m_t$.

$\log p(y_{1:T}) = \sum_t \log p(y_{t} | y_{1:t-1})$

Also, $p(y_{1:T}) = \sum_{j} p(x_T=j | y_{1:T})$.

## Backward (smoothing) algorithm

From the forward pass, we have computed $\alpha_t(j) = p(x_t = j| y_{1:t})$ and $\alpha_{t|t-1}(j) = p(x_t = j | y_{1:t-1})$.

The smoothing distribution:

\begin{align}
p(x_t | y_{1:T}) &= \frac{p(x_t, y_t, y_{t+1:T} | y_{1:t-1})}{p(y_{t:T+1} | y_{1:t-1})} \\
&\propto p(y_{t+1:T} | x_t) p(y_t | x_t) p(x_t | y_{1:t-1}) \\
&= \beta_t(x_t) p(y_t | x_t) \alpha_{t|t-1}(x_t) \\
&= \beta_t(x_t) p(y_t | x_t) (P^T \alpha_{t-1}).
\end{align}

We need a backward recursion to compute $\beta_t(x_t)$. 

\begin{align}
 \beta_t(i) &= p(y_{t+1:T} | x_t=i) \\
 &= \sum_{j} p(y_{t+1:T}, x_{t+1} = j | x_t=i) \\
 &= \sum_{j} p(y_{t+1} | x_{t+1} = j) p(y_{t+2:T} | x_{t+1}=j) p(x_{t+1} = j | x_t=i) \\
 &= \sum_{j} p(y_{t+1} | x_{t+1}=j) \beta_{t+1}(j) P_{ij}.
\end{align}

Base case $t = T$. Compute 

- Recursion: $\beta_T(j) = p(y_{T+1:T} | x_T) = p(\emptyset | x_T) = 1$.
- Smoothing: $p(x_T = j | y_{1:T}) \propto p(y_T | x_T = j) \alpha_{T|T-1}(j)$.

For $t < T$. Compute,

- Recursion: $\beta_t(i) = p(y_{t+1:T} | x_t = i) = \sum_{j} p(y_{t+1} | x_{t+1} = j) \beta_{t+1}(j) P_{ij}$.
- Smoothing: $p(x_t=i | y_{1:T}) \propto \beta_t(i) p(y_t | x_t = i) \alpha_{t|t-1}(i)$.




## Alternative forward algorithm

There is another version of the forward algorithm that computes $p(x_t, y_{1:t})$ at each time $t$ -- rather than computing $\alpha_{t}(x_t) = p(x_t | y_{1:t})$.

In that case, the recursion is given by

$$p(x_t, y_{1:t}) = \sum_{x_{t-1}} p(x_t, y_t, x_{t-1}, y_{1:t-1}) = \sum_{x_{t-1}} p(y_t|x_t) p(x_t|x_{t-1}) p(x_{t-1}, y_{1:t-1})$$

So 

$$\alpha_t(x_t) = \sum_{x_{t-1}} p(y_t|x_t) p(x_t|x_{t-1}) \alpha_{t-1}(x_{t-1}) = B(y_t) \odot (P^T \alpha_{t-1}),$$

where $B(y_t)$ denotes a vector of emission probabilities for each possible values of $x_t$.

Base case $t = 1$: compute $\alpha_1(x_1) = p(y_1 | x_1) p(x_1)$.

$t > 1$: compute $\alpha_t(x_t) = B(y_t) \odot (P^T \alpha_{t-1})$.

The backward algorithm remains the same.

$\beta_t(i) = p(y_{t+1:T} | x_t = i) = \sum_{j} p(y_{t+1} | x_{t+1} = j) \beta_{t+1}(j) P_{ij}$.

# EM algorithm

Complete log likelihood: $p(x_{1:T}, y_{1:T} | \theta) = p(x_1) \prod_{t > 1} p(x_t | x_{t-1}) \prod_{t \geq 1} p(y_t | x_t)$.

E-step: $Q(\theta | \theta^i) = \sum_{x_T} ... \sum_{x_1} p(x_{1:T} | y_{1:T}, \theta^i) \log p(x_{1:T}, y_{1:T} | \theta)$.

\begin{align}
    Q(\theta | \theta^i) &= \sum_{x_T} ... \sum_{x_1} p(x_1 | y_{1:T}, \theta^i) \prod_{t > 1} p(x_t | x_{t-1} y_{1:T}, \theta^i) [\log p(x_1|\theta) + \sum_{t > 1} \log p(x_t | x_{t-1}, \theta) + \sum_{t \geq 1} \log p(y_t | x_t, \theta)].
\end{align}

We will bring the prod into the braces and expand the terms one by one.

For the term $\log p(x_1 | \theta)$:

\begin{align}
    \sum_{x_T} ... \sum_{x_1} p(x_1 | y_{1:T}, \theta^i) \prod_{t > 1} p(x_t | x_{t-1} y_{1:T}, \theta^i) \log p(x_1|\theta) &= \sum_{x_1} p(x_1 | y_{1:T}, \theta^i) \log p(x_1 | \theta) \sum_{x_2} p(x_2 | x_1, y_{1:T}, \theta^i) \sum_{x_3} ... \sum_{x_T} p(x_{3:T} | x_2, y_{1:T}, \theta) \\
    &= \sum_{x_1} p(x_1 | y_{1:T}, \theta^i) \log p(x_1 | \theta).
\end{align}

For the term $\log p(x_2 | x_1, \theta)$:

\begin{align}
    \sum_{x_T} ... \sum_{x_1} p(x_1 | y_{1:T}, \theta^i) \prod_{t > 1} p(x_t | x_{t-1}, y_{1:T}, \theta^i) \log p(x_2|x_1, \theta) &= \sum_{x_1} \sum_{x_2} p(x_1 | y_{1:T}, \theta^i) p(x_2 | x_1, y_{1:T}, \theta^i) \log p(x_2 | x_1, \theta) \sum_{x_3} ... \sum_{x_T} p(x_{3:T} | x_2, y_{1:T}, \theta) \\
    &= \sum_{x_1} \sum_{x_2} p(x_1 | y_{1:T}, \theta^i) \frac{p(x_2, x_1 | y_{1:T}, \theta^i)}{p(x_1 | y_{1:T}, \theta^i)} \log p(x_2 | x_1, \theta) \\
    &= \sum_{x_1} \sum_{x_2} p(x_2, x_1 | y_{1:T}, \theta^i) \log p(x_2 | x_1, \theta).
\end{align}

We can generalize and see that we have the following terms for $t > 1$:

\begin{align}
    \sum_{x_{t-1}} \sum_{x_t} p(x_t, x_{t-1} | y_{1:T}, \theta^i) \log p(x_t | x_{t-1}, \theta).
\end{align}

Now, for the terms involving $y_1$:

\begin{align}
     \sum_{x_1} ... \sum_{x_T} p(x_1 | y_{1:T}, \theta^i) \prod_{t > 1} p(x_t | x_{t-1} y_{1:T}, \theta^i) \log p(y_1 | x_1, \theta) &=
     \sum_{x_1} p(x_1 | y_{1:T}, \theta^i) \log p(y_1 | x_1, \theta).
\end{align}

And for $y_t$ for $t > 1$:

\begin{align}
     \sum_{x_1} ... \sum_{x_T} p(x_1 | y_{1:T}, \theta^i) \prod_{t > 1} p(x_t | x_{t-1} y_{1:T}, \theta^i) \log p(y_t | x_t, \theta) &=
     \sum_{x_t} p(x_t | y_{1:T}, \theta^i) \log p(y_t | x_t, \theta).
\end{align}

Combine the terms and we have:

- $\sum_{x_1} p(x_1 | y_{1:T}, \theta^i) \log p(x_1 | \theta)$
- $\sum_{t > 1} \sum_{x_{t-1}} \sum_{x_t} p(x_t, x_{t-1} | y_{1:T}, \theta^i) \log p(x_t | x_{t-1}, \theta)$
- $\sum_{t \geq 1} \sum_{x_t} p(x_t | y_{1:T}, \theta^i) \log p(y_t | x_t, \theta)$.

Therefore, we need to compute $p(x_t | y_{1:T}, \theta^i)$, $p(x_t, x_{t-1} | y_{1:T}, \theta^i)$. To that end, we utilize Forward-Backward algorithm.



- Forward algorithm produces $\alpha_t(x_t) = p(x_t, y_{1:t} | \theta^i)$.
- Backward algorithm produces $\beta_t(x_t) = p(y_{t+1:T} | x_t, \theta^i)$.

So,

\begin{align}
\alpha_{t-1}(x_{t-1}) p(x_t | x_{t-1}) \beta_t(x_t) &= p(x_{t-1}, y_{1:t-1} | \theta^i) p(x_t | x_{t-1}, \theta^i) p(y_t | x_t, \theta^i) p(y_{t+1:T} | x_t, \theta^i) \\
&= p(x_{t-1}, x_t, y_{1:T})
\end{align}

Sum over $x_{t-1}, x_t$ and we get $p(y_{1:T})$ -- this is also available at the end of forward step.

\begin{align}
    \xi_{t-1,t} = p(x_{t-1}, x_t | y_{1:T}, \theta^i) = \frac{\alpha_{t-1}(x_{t-1}) p(x_t | x_{t-1}, \theta^i) p(y_t | x_t, \theta^i) \beta_t(x_t)}{p(y_{1:T} | \theta^i)}
\end{align}

Note: it might be more intuitive to compute $\xi_{t,t+1}$.

We can obtain $p(x_t | y_{1:T}, \theta^i)$ by: 

$$\gamma_t = p(x_t | y_{1:T}, \theta^i) = \frac{\alpha_t(x_t) \beta_t(x_t)}{p(y_{1:T} | \theta^i)} = \frac{p(x_t, y_{1:T}|\theta^i)}{p(y_{1:T} | \theta^i)}$$




To update $\mu$, only $\log p(x_1 | \theta) = \mu_{x_1}$ needs to be optimized.

$\hat{\mu}_k = \text{argmax}_{\mu_k} \sum_{k} \gamma_t^i(k) \log \mu_k - \kappa (\sum_k \mu_k - 1)$

This yields $\mu_k = \gamma_t^i(k) / \kappa$ where $\kappa = \sum_k \gamma_t^i(k) = 1$.

Derive update for the Poisson parameters $\lambda$.